In [2]:
import sys
!{sys.executable} -m pip install --upgrade google-cloud-storage
%env GOOGLE_APPLICATION_CREDENTIALS=/Users/willyraedy/Sync/SideProjects/RedditResearch/credentials-ebeb319739c4.json
import time
import pandas as pd
import sys
import praw
import glob
import math
import os
from google.cloud import storage

Requirement already up-to-date: google-cloud-storage in /Users/willyraedy/anaconda3/lib/python3.7/site-packages (1.23.0)
env: GOOGLE_APPLICATION_CREDENTIALS=/Users/willyraedy/Sync/SideProjects/RedditResearch/credentials-ebeb319739c4.json


In [4]:
bucket = storage.Client().get_bucket('meli_thesis')
blobs = bucket.list_blobs(prefix='withWikis')

In [9]:
bucket = storage.Client().get_bucket('meli_thesis')
blobs = bucket.list_blobs(prefix='withWikis')

dataframes = []

for blob in blobs:
    temp_filename = 'foobar.csv'
    blob.download_to_filename(temp_filename)
    next_df = pd.read_csv(temp_filename)
    dataframes.append(next_df)
    os.remove(temp_filename)
    
all_with_wikis = pd.concat(dataframes)
    

In [7]:
def upload_to_gcp(dataframe, gcp_filename):
    try:
        dataframe.to_csv(gcp_filename)

        blob = bucket.blob(gcp_filename)
        blob.upload_from_filename(gcp_filename)

        os.remove(gcp_filename)
    except:
        e = sys.exc_info()[0]
        print(e)
        print('Temp file was not deleted (probably)')

In [10]:
all_with_wikis.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 182862 entries, 0 to 18278
Data columns (total 10 columns):
Unnamed: 0          182862 non-null int64
index               182862 non-null int64
Unnamed: 0.1        182862 non-null int64
Unnamed: 0.1.1      182862 non-null int64
real_name           182861 non-null object
desc                148912 non-null object
created_date        182862 non-null object
subs                182862 non-null int64
description_html    137579 non-null object
wiki_text           29725 non-null object
dtypes: int64(5), object(5)
memory usage: 15.3+ MB


In [93]:
import re

with_word_breaks = list(map(lambda w: r'\b' + w + r'\b', network_seed_list))
print(with_word_breaks)
regex = re.compile('|'.join(with_word_breaks))

def filter_network_reddits(dataframe):
    return dataframe[dataframe['description_html'].str.contains(regex, na=False) | dataframe['wiki_text'].str.contains(regex, na=False)]

['\\br/latinoamerica\\b', '\\br/argentina\\b', '\\br/bolivia\\b', '\\br/brasil\\b', '\\br/chile\\b', '\\br/colombia\\b', '\\br/costa_rica\\b', '\\br/cuba\\b', '\\br/dominican\\b', '\\br/ecuador\\b', '\\br/estadosunidos\\b', '\\br/elsalvador\\b', '\\br/es\\b', '\\br/guatemala\\b', '\\br/honduras\\b', '\\br/mexico\\b', '\\br/nicaragua\\b', '\\br/panama\\b', '\\br/paraguay\\b', '\\br/peru\\b', '\\br/puertorico\\b', '\\br/spain\\b', '\\br/uruguay\\b', '\\br/venezuela\\b', '\\br/LatinAmerica\\b', '\\br/redditores\\b', '\\br/espanol\\b', '\\br/catolicismo\\b', '\\br/futbol\\b', '\\br/videojuego\\b', '\\br/musicaenespanol\\b']


In [94]:
network = filter_network_reddits(all_with_wikis)

In [95]:
network.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 162 entries, 4021 to 15421
Data columns (total 10 columns):
Unnamed: 0          162 non-null int64
index               162 non-null int64
Unnamed: 0.1        162 non-null int64
Unnamed: 0.1.1      162 non-null int64
real_name           162 non-null object
desc                138 non-null object
created_date        162 non-null object
subs                162 non-null int64
description_html    161 non-null object
wiki_text           86 non-null object
dtypes: int64(5), object(5)
memory usage: 13.9+ KB


In [96]:
network.head(50)

Unnamed: 0   index  Unnamed: 0.1  Unnamed: 0.1.1          real_name  \
4021         4021   47152         47152         1227877           Tabarnia   
6662         6662   74545         74545         1255270    SpainAuxiliares   
10965       10965  117241        117241         1297966            transbr   
15670       15670  163485        163485         1344210        ayudamexico   
53          18340  189428         20753          358103    CaribbeanTravel   
200         18487  190893         22218          359568        PictureGame   
1740        20027  206805         38130          375480        GoldTesting   
2503        20790  217031         48356          385706              fulbo   
4637        22924  235555         66880          404230           canarias   
7260        25547  258823         90148          427498    chilecirclejerk   
10678       28965  290598        121923          459273   ListOfSubreddits   
15549       33836  338857          1507          170182            direito   
482         37056  373194         35844          204519  LGBT_de_Argentina   
3361        39935  393767         56417          225092        TechoBlanco   
4475        41049  401015         63665          232340      ModeratorDuck   
5760        42334  409131         71781          240456     brazilianmusic   
7247        43821  419262         81912          250587         ateismo_br   
8819        45393  428563         91213          259888    CatholicAnswers   
9186        45760  430776         93426          262101          CoquiJerk   
10524       47098  440195        102845          271520        catolicismo   
11107       47681  444424        107074          275749        holdthemoan   
14450       51024  467907        130557          299232           pocmedia   
96          54957  498615        161265          329940           dogecoin   
806         55667  504120        166770          335445        so_doge_tip   
3317        58178  528780         22755          528780            Bovespa   
4506        59367  541955         35930          541955       escrevasobre   
4776        59637  544957         38932          544957         brasilivre   
5399        60260  552916         46891          552916      maite_perroni   
5706        60567  556205         50180          556205             TheNAU   
8276        63137  582560         76535          582560            brasil2   
9242        64103  595453         89428          595453          brasil420   
9410        64271  598618         92593          598618       RolEnEspanol   
10233       65094  618579        112554          618579           newsokur   
10911       65772  630677        124652          630677    Uncensored_News   
14396       69257  664893        158868          664893         foradecasa   
15510       70371  674756            56              56             soccer   
15622       70483  674868           168             168     SubredditDrama   
15813       70674  675059           359             359             mexico   
15831       70692  675077           377             377             europe   
16248       71109  675494           794             794            Denmark   
16529       71390  675776          1076            1076          argentina   
16831       71692  676078          1378            1378        findareddit   
17765       72626  677024          2324            2324             greece   
17814       72675  677074          2374            2374              italy   
17852       72713  677112          2412            2412        puerto_rico   
17924       72785  677184          2484            2484  animalesdeconsejo   
277         73425  677850          3150            3150            Spanish   
566         73714  678166          3466            3466            belgium   
936         74084  678607          3907            3907             Brazil   
1143        74291  678849          4149            4149              chile   

                            

In [92]:
v = network[network['real_name'] == 'kpop']['wiki_text'].values[0]
regex.search(v)
v

'# Achievements\r\n\r\n[LINK BACK TO MAIN RULES WIKI](https://www.reddit.com/r/kpop/wiki/rules)\r\n\r\nThis page contains the extended guidelines/rules for the achievement-related content on r/kpop.\r\n\r\nWhen submitting Achievements content, please wait for an official announcement or a news article as often as possible. Make sure you are linking reliable sources. Moderators may remove your submission if any claims are unsubstantiated or may be subject to change before an official announcement is made.\r\n\r\n**Please use the `[Achievement]` flair for your posts!**\r\n\r\n&nbsp;\r\n\r\n### Restricted Content\r\n\r\n**Achievements in this list are restricted to the automated [“Weekly Charts and Achievements”](https://www.reddit.com/r/kpop/search?q=title%3A%22charts+and+achievements%22&restrict_sr=on&sort=new&t=all) posts which are posted on Fridays:**\r\n\r\n* Instiz Real-time and Certified All Kills\r\n* Brand Reputation Rankings\r\n* Streaming Records (Spotify, Oricon, Soundcloud, e

In [34]:
network_seed_list = [
'r/latinoamerica',
'r/argentina',
'r/bolivia',
'r/brasil',
'r/chile',
'r/colombia',
'r/costa_rica',
'r/cuba',
'r/dominican',
'r/ecuador',
'r/estadosunidos',
'r/elsalvador',
'r/es',
'r/guatemala',
'r/honduras',
'r/mexico',
'r/nicaragua',
'r/panama',
'r/paraguay',
'r/peru',
'r/puertorico',
'r/spain',
'r/uruguay',
'r/venezuela',
'r/LatinAmerica',
'r/redditores',
'r/espanol',
'r/catolicismo',
'r/futbol',
'r/videojuego',
'r/musicaenespanol',
]

In [46]:
import re

regex = re.compile('|'.join(network_seed_list))

In [49]:
regex.search('r/argentina')

<re.Match object; span=(0, 11), match='r/argentina'>